In [1]:
import numpy as np
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt
%matplotlib inline
import pandas_profiling
from sklearn.linear_model import LinearRegression
from sklearn.datasets import load_boston
from sklearn.metrics import mean_squared_error, mean_absolute_error, r2_score
from sklearn import preprocessing

# 1. Загрузим исходные данные и посмотрим статистику

In [2]:
df = pd.read_csv('aac_shelter_outcomes.csv', sep = ',')
df.head()

age_upon_outcome animal_id animal_type                    breed  \
0          2 weeks   A684346         Cat   Domestic Shorthair Mix   
1           1 year   A666430         Dog               Beagle Mix   
2           1 year   A675708         Dog                 Pit Bull   
3          9 years   A680386         Dog  Miniature Schnauzer Mix   
4         5 months   A683115       Other                  Bat Mix   

          color        date_of_birth             datetime  \
0  Orange Tabby  2014-07-07T00:00:00  2014-07-22T16:04:00   
1   White/Brown  2012-11-06T00:00:00  2013-11-07T11:47:00   
2    Blue/White  2013-03-31T00:00:00  2014-06-03T14:20:00   
3         White  2005-06-02T00:00:00  2014-06-15T15:50:00   
4         Brown  2014-01-07T00:00:00  2014-07-07T14:04:00   

             monthyear     name outcome_subtype outcome_type sex_upon_outcome  
0  2014-07-22T16:04:00      NaN         Partner     Transfer      Intact Male  
1  2013-11-07T11:47:00     Lucy         Partner     Transfer    Spayed Female  
2  2014-06-03T14:20:00  *Johnny             NaN     Adoption    Neutered Male  
3  2014-06-15T15:50:00   Monday         Partner     Transfer    Neutered Male  
4  2014-07-07T14:04:00      NaN     Rabies Risk   Euthanasia          Unknown

In [3]:
df_rep = df.profile_report()

In [4]:
df_rep

# 2. Очистим данные и остаим только 'Adoption' и 'Transfer'

In [5]:
df_lab = df.loc[df['outcome_type'].isin(['Adoption', 'Transfer'])]
df_lab.head()

age_upon_outcome animal_id animal_type                    breed  \
0          2 weeks   A684346         Cat   Domestic Shorthair Mix   
1           1 year   A666430         Dog               Beagle Mix   
2           1 year   A675708         Dog                 Pit Bull   
3          9 years   A680386         Dog  Miniature Schnauzer Mix   
5         4 months   A664462         Dog           Leonberger Mix   

          color        date_of_birth             datetime  \
0  Orange Tabby  2014-07-07T00:00:00  2014-07-22T16:04:00   
1   White/Brown  2012-11-06T00:00:00  2013-11-07T11:47:00   
2    Blue/White  2013-03-31T00:00:00  2014-06-03T14:20:00   
3         White  2005-06-02T00:00:00  2014-06-15T15:50:00   
5   Brown/White  2013-06-03T00:00:00  2013-10-07T13:06:00   

             monthyear     name outcome_subtype outcome_type sex_upon_outcome  
0  2014-07-22T16:04:00      NaN         Partner     Transfer      Intact Male  
1  2013-11-07T11:47:00     Lucy         Partner     Transfer    Spayed Female  
2  2014-06-03T14:20:00  *Johnny             NaN     Adoption    Neutered Male  
3  2014-06-15T15:50:00   Monday         Partner     Transfer    Neutered Male  
5  2013-10-07T13:06:00   *Edgar         Partner     Transfer      Intact Male

In [6]:
df_rep_lab = df_lab.profile_report()
df_rep_lab

Переведем Временные признаки из Категориального формата в формат Дата-время

In [7]:
df_lab['datetime'] = pd.to_datetime(df_lab['datetime'])
df_lab['monthyear'] = pd.to_datetime(df_lab['monthyear'])
df_lab['date_of_birth'] = pd.to_datetime(df_lab['date_of_birth'])

C:\Users\rus17\Anaconda3\lib\site-packages\ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.
C:\Users\rus17\Anaconda3\lib\site-packages\ipykernel_launcher.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  
C:\Users\rus17\Anaconda3\lib\site-packages\ipykernel_launcher.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in t

Признак 'date_of_birth' связан с признаком 'age_upon_outcome'. Посчитаем в днях возраст животного, запишем в новый признак 'age_days' и оставим его в датасете, признаки 'date_of_birth' и 'age_upon_outcome' удалим.

In [8]:
df_lab['age_days'] = (df_lab['datetime']-df_lab['date_of_birth']) / np.timedelta64(1, 'D')

C:\Users\rus17\Anaconda3\lib\site-packages\ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.


In [9]:
df_lab['age_days'].describe()

count    56611.000000
mean       633.373059
std        907.927571
min       -122.445139
25%         78.778472
50%        312.771528
75%        742.748264
max       9137.000000
Name: age_days, dtype: float64

в новом признаке получились отрицательные и нулевые значения.

In [10]:
df_lab[df_lab['age_days']==0]

Empty DataFrame
Columns: [age_upon_outcome, animal_id, animal_type, breed, color, date_of_birth, datetime, monthyear, name, outcome_subtype, outcome_type, sex_upon_outcome, age_days]
Index: []

можно сделать предположение, что это новорожденные животные.

Посмотрим отрицательные значения

In [11]:
df_lab[df_lab['age_days']<0]

age_upon_outcome animal_id animal_type                   breed  \
19814          0 years   A660928         Dog  Labrador Retriever Mix   
22804          0 years   A751749         Dog       Border Collie Mix   
45764          0 years   A737397         Cat  Domestic Shorthair Mix   
50533          0 years   A706929         Cat  Domestic Shorthair Mix   
52977          0 years   A736114         Cat  Domestic Shorthair Mix   
64745          0 years   A702326         Cat  Domestic Shorthair Mix   

              color date_of_birth            datetime           monthyear  \
19814   Black/White    2014-04-03 2013-12-01 13:19:00 2013-12-01 13:19:00   
22804   Black/White    2014-12-12 2014-09-10 17:29:00 2014-09-10 17:29:00   
45764  White/Orange    2016-11-15 2016-11-05 18:16:00 2016-11-05 18:16:00   
50533        Tortie    2015-07-06 2015-07-05 14:46:00 2015-07-05 14:46:00   
52977  Orange Tabby    2016-10-28 2016-10-04 15:13:00 2016-10-04 15:13:00   
64745         Black    2015-08-29 2015-05-24 17:01:00 2015-05-24 17:01:00   

            name outcome_subtype outcome_type sex_upon_outcome    age_days  
19814      Sadie         Partner     Transfer    Spayed Female -122.445139  
22804       Juan             NaN     Adoption    Neutered Male  -92.271528  
45764  Jellybean             NaN     Adoption    Intact Female   -9.238889  
50533        NaN         Partner     Transfer          Unknown   -0.384722  
52977        NaN         Partner     Transfer      Intact Male  -23.365972  
64745   Penelope             NaN     Adoption    Spayed Female  -96.290972

Для строчек 2, 3, 4 можно сделать предположение, что это ошибка ввода и эти животные, скорее всего новорожденные (на основе значения 'Intact' в значение пола животного. Поэтому начначим им age_days=0 и запишем date_of_birth равным monthyear

In [12]:
df_lab.loc[[45764, 50533, 52977], 'age_days'] = 0.1
df_lab.loc[[45764, 50533, 52977], 'date_of_birth'] = df_lab.loc[[45764, 50533, 52977], 'monthyear']
df_lab.loc[[45764, 50533, 52977]]

C:\Users\rus17\Anaconda3\lib\site-packages\pandas\core\indexing.py:494: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.obj[item] = s


age_upon_outcome animal_id animal_type                   breed  \
45764          0 years   A737397         Cat  Domestic Shorthair Mix   
50533          0 years   A706929         Cat  Domestic Shorthair Mix   
52977          0 years   A736114         Cat  Domestic Shorthair Mix   

              color       date_of_birth            datetime  \
45764  White/Orange 2016-11-05 18:16:00 2016-11-05 18:16:00   
50533        Tortie 2015-07-05 14:46:00 2015-07-05 14:46:00   
52977  Orange Tabby 2016-10-04 15:13:00 2016-10-04 15:13:00   

                monthyear       name outcome_subtype outcome_type  \
45764 2016-11-05 18:16:00  Jellybean             NaN     Adoption   
50533 2015-07-05 14:46:00        NaN         Partner     Transfer   
52977 2016-10-04 15:13:00        NaN         Partner     Transfer   

      sex_upon_outcome  age_days  
45764    Intact Female       0.1  
50533          Unknown       0.1  
52977      Intact Male       0.1

Рассмотрим оставшиеся отрицательные значения

In [13]:
df_lab[df_lab['age_days']<0]

age_upon_outcome animal_id animal_type                   breed  \
19814          0 years   A660928         Dog  Labrador Retriever Mix   
22804          0 years   A751749         Dog       Border Collie Mix   
64745          0 years   A702326         Cat  Domestic Shorthair Mix   

             color date_of_birth            datetime           monthyear  \
19814  Black/White    2014-04-03 2013-12-01 13:19:00 2013-12-01 13:19:00   
22804  Black/White    2014-12-12 2014-09-10 17:29:00 2014-09-10 17:29:00   
64745        Black    2015-08-29 2015-05-24 17:01:00 2015-05-24 17:01:00   

           name outcome_subtype outcome_type sex_upon_outcome    age_days  
19814     Sadie         Partner     Transfer    Spayed Female -122.445139  
22804      Juan             NaN     Adoption    Neutered Male  -92.271528  
64745  Penelope             NaN     Adoption    Spayed Female  -96.290972

Это явно взрослые животные, т.к. они стерелизованые, значит ошибка в вводе зничений их даты рождения.

# 3. Проверим есть ли разница между признаками 'datetime' и 'monthyear'

In [14]:
(df_lab['datetime']-df_lab['monthyear']).describe()

count              56611
mean     0 days 00:00:00
std      0 days 00:00:00
min      0 days 00:00:00
25%      0 days 00:00:00
50%      0 days 00:00:00
75%      0 days 00:00:00
max      0 days 00:00:00
dtype: object

Признаки совподают, поэтому оставим только один из них.

In [16]:
df_lab = df_lab.drop(['datetime'], axis=1)
df_lab = df_lab.drop(['animal_id'], axis=1)
df_lab = df_lab.drop(['outcome_subtype'], axis=1)
df_lab = df_lab.drop(['date_of_birth'], axis=1)
df_lab = df_lab.drop(['age_upon_outcome'], axis=1)
df_lab = df_lab.drop(['name'], axis=1)

In [17]:
df_lab.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 56611 entries, 0 to 78255
Data columns (total 7 columns):
animal_type         56611 non-null object
breed               56611 non-null object
color               56611 non-null object
monthyear           56611 non-null datetime64[ns]
outcome_type        56611 non-null object
sex_upon_outcome    56611 non-null object
age_days            56611 non-null float64
dtypes: datetime64[ns](1), float64(1), object(5)
memory usage: 6.0+ MB


In [18]:
df_lab.profile_report()

Предположим, что на целевой признак влияют в основном animal_type и age_days и будем предсказывать на основе этих признаков.

In [19]:
df_lern = df_lab[['animal_type', 'age_days', 'outcome_type']].reset_index()

In [20]:
df_lern

index animal_type     age_days outcome_type
0          0         Cat    15.669444     Transfer
1          1         Dog   366.490972     Transfer
2          2         Dog   429.597222     Adoption
3          3         Dog  3300.659722     Transfer
4          5         Dog   126.545833     Transfer
...      ...         ...          ...          ...
56606  78250         Dog    59.777778     Adoption
56607  78251         Dog    59.768056     Adoption
56608  78252         Dog  1129.754167     Adoption
56609  78254         Dog    80.772222     Adoption
56610  78255         Dog    80.780556     Adoption

[56611 rows x 4 columns]

In [21]:
cd = df_lern['animal_type'].get_values().reshape(-1,1)
one_en = preprocessing.OneHotEncoder()
one_en.fit(cd)
one_res = one_en.transform(cd).toarray()

C:\Users\rus17\Anaconda3\lib\site-packages\ipykernel_launcher.py:1: FutureWarning: The 'get_values' method is deprecated and will be removed in a future version. Use '.to_numpy()' or '.array' instead.
  """Entry point for launching an IPython kernel.


In [22]:
df_one = pd.DataFrame(one_res, columns=['animal_type_1','animal_type_2','animal_type_3','animal_type_4','animal_type_5',])

In [23]:
df_lern = pd.concat([df_lern, df_one], axis=1)

In [24]:
mm_en = preprocessing.LabelEncoder()
cd = df_lern['outcome_type'].get_values().reshape(-1,1)
mm_en.fit(cd)
en_res = mm_en.transform(cd)

C:\Users\rus17\Anaconda3\lib\site-packages\ipykernel_launcher.py:2: FutureWarning: The 'get_values' method is deprecated and will be removed in a future version. Use '.to_numpy()' or '.array' instead.
  
C:\Users\rus17\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:219: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\rus17\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:252: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


In [25]:
df_en = pd.DataFrame(en_res, columns=['outcome_type_L'])

In [26]:
df_lern = pd.concat([df_lern, df_en], axis=1)
df_lern

index animal_type     age_days outcome_type  animal_type_1  \
0          0         Cat    15.669444     Transfer            0.0   
1          1         Dog   366.490972     Transfer            0.0   
2          2         Dog   429.597222     Adoption            0.0   
3          3         Dog  3300.659722     Transfer            0.0   
4          5         Dog   126.545833     Transfer            0.0   
...      ...         ...          ...          ...            ...   
56606  78250         Dog    59.777778     Adoption            0.0   
56607  78251         Dog    59.768056     Adoption            0.0   
56608  78252         Dog  1129.754167     Adoption            0.0   
56609  78254         Dog    80.772222     Adoption            0.0   
56610  78255         Dog    80.780556     Adoption            0.0   

       animal_type_2  animal_type_3  animal_type_4  animal_type_5  \
0                1.0            0.0            0.0            0.0   
1                0.0            1.0            0.0            0.0   
2                0.0            1.0            0.0            0.0   
3                0.0            1.0            0.0            0.0   
4                0.0            1.0            0.0            0.0   
...              ...            ...            ...            ...   
56606            0.0            1.0            0.0            0.0   
56607            0.0            1.0            0.0            0.0   
56608            0.0            1.0            0.0            0.0   
56609            0.0            1.0            0.0            0.0   
56610            0.0            1.0            0.0            0.0   

       outcome_type_L  
0                   1  
1                   1  
2                   0  
3                   1  
4                   1  
...               ...  
56606               0  
56607               0  
56608               0  
56609               0  
56610               0  

[56611 rows x 10 columns]

In [27]:
df_lern = df_lern.drop(['index'], axis=1)
df_lern = df_lern.drop(['animal_type'], axis=1)
df_lern = df_lern.drop(['outcome_type'], axis=1)
df_lern.head()

age_days  animal_type_1  animal_type_2  animal_type_3  animal_type_4  \
0    15.669444            0.0            1.0            0.0            0.0   
1   366.490972            0.0            0.0            1.0            0.0   
2   429.597222            0.0            0.0            1.0            0.0   
3  3300.659722            0.0            0.0            1.0            0.0   
4   126.545833            0.0            0.0            1.0            0.0   

   animal_type_5  outcome_type_L  
0            0.0               1  
1            0.0               1  
2            0.0               0  
3            0.0               1  
4            0.0               1

# 5. Применим метод k-ближайших соседей.

In [28]:
from sklearn.neighbors import KNeighborsClassifier  
from sklearn.model_selection import train_test_split

In [29]:
X_train, X_test, Y_train, Y_test = train_test_split(df_lern[df_lern.columns[0:6]], df_lern['outcome_type_L'], test_size = 0.2, random_state=5)
model = KNeighborsClassifier(n_neighbors=2)
model.fit(X_train, Y_train)

KNeighborsClassifier(algorithm='auto', leaf_size=30, metric='minkowski',
                     metric_params=None, n_jobs=None, n_neighbors=2, p=2,
                     weights='uniform')

In [30]:
from sklearn.metrics import accuracy_score 
y_train_predict = model.predict(X_train)
y_test_predict = model.predict(X_test)
print('Ошибка на тренировочной выборке = {}'.format(accuracy_score(y_train_predict, Y_train)))
print('Ошибка на тестевой выборке = {}'.format(accuracy_score(y_test_predict, Y_test)))

Ошибка на тренировочной выборке = 0.8754636989931107
Ошибка на тестевой выборке = 0.7673761370661486


Результаты неплохие. Попробуем улучшить.

# 6. Построим модель Случайного леса

In [32]:
from sklearn.ensemble import RandomForestClassifier

In [33]:
model = RandomForestClassifier(n_estimators=100, 
                               bootstrap = True,
                               max_features = 'sqrt')
model.fit(X_train, Y_train)

RandomForestClassifier(bootstrap=True, class_weight=None, criterion='gini',
                       max_depth=None, max_features='sqrt', max_leaf_nodes=None,
                       min_impurity_decrease=0.0, min_impurity_split=None,
                       min_samples_leaf=1, min_samples_split=2,
                       min_weight_fraction_leaf=0.0, n_estimators=100,
                       n_jobs=None, oob_score=False, random_state=None,
                       verbose=0, warm_start=False)

In [34]:
y_train_predict = model.predict(X_train)
y_test_predict = model.predict(X_test)

In [ ]:
Рассчитаем ошибку roc_auc_score

In [35]:
from sklearn.metrics import roc_auc_score

roc_value_train = roc_auc_score(Y_train, y_train_predict)
roc_value_test = roc_auc_score(Y_test, y_test_predict)
print('Ошибка roc auc на тренировочной выборке = {}'.format(roc_value_train))
print('Ошибка roc auc на тестевой выборке = {}'.format(roc_value_test))

Ошибка roc auc на тренировочной выборке = 0.9853953634755697
Ошибка roc auc на тестевой выборке = 0.7483270584008238


Данная модель не смогла улучшить предыдущую модель, значит есть смысл использовать метод k-ближайших соседей.